In [1]:
%load_ext autoreload
%autoreload 2

import numpy as np
from strategy_v2.Strategy import *
from strategy_v2.TradingSubSystem import *
from strategy_v2.Portfolio import *
from strategy_v2.TransactionCost import *
from strategy_v2.Executor import *
from utils.data_helper import *
from utils.data import *
from utils.performance import *
import cvxpy as cp
from plotly.subplots import make_subplots
from croniter import croniter

# Portfolio General Settings
We assume the code is run at T before market open, so it all data on and before T-1 close. Therefore, the end_date should be today - BDay(1)

In [2]:
end_date = get_today()
start_date = pd.to_datetime(datetime(2022, 1, 3))
vol_target = 0.5
max_leverage = 1

# Linear Optimization (Risk-Adjusted Return)

- How to determine the capital?

Difficulty here is portfolio might use different leverage per rebalance, looking at the asset MV might not give you the total portfolio capital (e.g. 70% leverage, your stocks only worth 70% of your capital now)

we can use the market value on Futu divides by the leverage used for last periods. This will give you the total captial for the portfolio

Then we use this capital for next rebalance

We shuold strategically fix this issue by reading capital from Futu or keep track the capital ourselves

- 2024-03-23 - Leverage Ratio = 102.4376
- 2024-04-20 - Leverage Ratio = 102.6119
- 2024-05-03 - Leverage Ratio = 97.8875
- 2024-05-17 - Leverage Ratio = 99.1256
- 2024-05-31 - Leverage Ratio = 102.182
- 2024-06-14 - Leverage Ratio = 101.4418
- 2024-07-20 - Leverage Ratio = 95.64553
- 2024-08-09 - Leverage Ratio = 94.7114
- 2024-08-23 - Leverage Ratio = 99.3433

In [3]:
portfolio = PortfolioMeanVarOpt(
    capital=169336.48958837058,
    name='ETF Buy and Hold Portfolio',
    lookback_period=60,
    opt_freq=1,
    rebalance_iter=RebalancerIter('0 0 * * Fri', 2),    
    tc_model=TransactionCostFutu(),    
    systems=[
        TradingSubSystemSingle(vol_target=vol_target, instruments=['META'],  strategy=[BuyAndHoldStrategy(confidence=1)], max_leverage=max_leverage),
        TradingSubSystemSingle(vol_target=vol_target, instruments=['TSLA'],  strategy=[BuyAndHoldStrategy(confidence=1)], max_leverage=max_leverage),
        TradingSubSystemSingle(vol_target=vol_target, instruments=['NVDA'],  strategy=[BuyAndHoldStrategy(confidence=1)], max_leverage=max_leverage),
        TradingSubSystemSingle(vol_target=vol_target, instruments=['AAPL'],  strategy=[BuyAndHoldStrategy(confidence=1)], max_leverage=max_leverage),
        TradingSubSystemSingle(vol_target=vol_target, instruments=['EWY'],   strategy=[BuyAndHoldStrategy(confidence=1)], max_leverage=max_leverage),
        TradingSubSystemSingle(vol_target=vol_target, instruments=['DXJ'],   strategy=[BuyAndHoldStrategy(confidence=2)], max_leverage=max_leverage),        
        #TradingSubSystemSingle(vol_target=vol_target, instruments=['VOE'],   strategy=[BuyAndHoldStrategy(confidence=1)], max_leverage=max_leverage),
        #TradingSubSystemSingle(vol_target=vol_target, instruments=['VBR'],   strategy=[BuyAndHoldStrategy(confidence=1)], max_leverage=max_leverage),
        TradingSubSystemSingle(vol_target=vol_target, instruments=['BRK-B'], strategy=[BuyAndHoldStrategy(confidence=2)], max_leverage=max_leverage),
        TradingSubSystemSingle(vol_target=vol_target, instruments=['SPY'],   strategy=[BuyAndHoldStrategy(confidence=1)], max_leverage=max_leverage),
        TradingSubSystemSingle(vol_target=vol_target, instruments=['QQQ'],   strategy=[BuyAndHoldStrategy(confidence=1)], max_leverage=max_leverage),        
])

portfolio.set_start_date(start_date)
portfolio.set_end_date(end_date)
portfolio.backtest_subsystems()
portfolio.optimize(gamma=10, hhi=0.2)
portfolio.backtest()
portfolio.rebalance()
portfolio.performance(show_all_rets=True)

[*********************100%***********************]  1 of 1 completed

2024-08-26 02:18:38,031 - TradingSubSystemSingle [META (BAH1)] - INFO - Generating position for strategy BAH1 between 2021-10-04 and 2024-08-25......
2024-08-26 02:18:38,039 - TradingSubSystemSingle [META (BAH1)] - INFO - Volatility Target = 50.0% | Price Volatility = 33.7% | Last Scale Factor = 1.47



[*********************100%***********************]  1 of 1 completed

2024-08-26 02:18:38,248 - TradingSubSystemSingle [TSLA (BAH1)] - INFO - Generating position for strategy BAH1 between 2021-10-04 and 2024-08-25......
2024-08-26 02:18:38,254 - TradingSubSystemSingle [TSLA (BAH1)] - INFO - Volatility Target = 50.0% | Price Volatility = 65.4% | Last Scale Factor = 0.79



[*********************100%***********************]  1 of 1 completed

...


[*********************100%***********************]  1 of 1 completed

2024-08-26 02:18:40,006 - TradingSubSystemSingle [QQQ (BAH1)] - INFO - Generating position for strategy BAH1 between 2021-10-04 and 2024-08-25......
2024-08-26 02:18:40,014 - TradingSubSystemSingle [QQQ (BAH1)] - INFO - Volatility Target = 50.0% | Price Volatility = 28.3% | Last Scale Factor = 1.77


100%|██████████| 690/690 [00:03<00:00, 184.54it/s]


[*********************100%***********************]  1 of 1 completed
[*********************100%***********************]  1 of 1 completed


Rebalanced Portfolio  Optimized Portfolio      ^SPX   
Measure                                                                        
Cumulative Return                    1.877773             1.852700  1.174719  \
Annualized Return                    0.262813             0.257520  0.077397   
Annualized Volatility                0.217728             0.216810  0.180336   
Annualized Sharpe Ratio              1.052350             1.032390  0.242377   
Maximum Drawdown                    -0.262382            -0.272074 -0.254251   

                         META (BAH1)  TSLA (BAH1)  NVDA (BAH1)  AAPL (BAH1)   
Measure                                                                       
Cumulative Return           1.667553     0.677860     4.214906     1.296655  \
Annualized Return           0.311468    -0.021843     0.667291     0.137722   
Annualized Volatility       0.479434     0.500809     0.496237     0.280032   
Annualized Sharpe Ratio     0.579392    -0.110881     1.276814     0.371510   
Maximum Drawdown           -0.682479    -0.635372    -0.531787    -0.309294   

                         EWY (BAH1)  DXJ (BAH2)  BRK-B (BAH2)  SPY (BAH1)   
Measure                                                                     
Cumulative Return          0.896366    1.830099      1.516321    1.228757  \
Annualized Return         -0.011899    0.245568      0.173317    0.094504   
Annualized Volatility      0.243471    0.179013      0.174922    0.180529   
Annualized Sharpe Ratio   -0.187238    1.183603      0.798240    0.336881   
Maximum Drawdown          -0.406293   -0.221939     -0.265790   -0.244964   

                         QQQ (BAH1)  
Measure                              
Cumulative Return          1.227339  
Annualized Return          0.107506  
Annualized Volatility      0.243823  
Annualized Sharpe Ratio    0.302756  
Maximum Drawdown          -0.348280

In [10]:
portfolio.get_position_for_trade()

2024-08-24 00:45:44,970 - Linear Optimized Portfolio (ETF Buy and Hold Portfolio) - CRITICAL - Portfolio target capital is not specified, use initial backtest capital of $169,336
2024-08-24 00:45:44,971 - Linear Optimized Portfolio (ETF Buy and Hold Portfolio) - INFO - Generate trade position based on target capital of $169,336


META  TSLA   NVDA   AAPL   EWY   DXJ  BRK-B   SPY   QQQ
Date                                                               
2022-01-03   0.0  45.0  824.0  278.0  11.0  80.0  120.0  43.0  12.0
2022-01-04   0.0  45.0  824.0  278.0  11.0  80.0  120.0  43.0  12.0
2022-01-05   0.0  45.0  824.0  278.0  11.0  80.0  120.0  43.0  12.0
2022-01-06   0.0  45.0  824.0  278.0  11.0  80.0  120.0  43.0  12.0
2022-01-07   0.0  45.0  824.0  278.0  11.0  80.0  120.0  43.0  12.0
...          ...   ...    ...    ...   ...   ...    ...   ...   ...
2024-08-19  38.0  52.0  107.0  182.0   0.0   0.0  120.0  43.0   4.0
2024-08-20  38.0  52.0  107.0  182.0   0.0   0.0  120.0  43.0   4.0
2024-08-21  38.0  52.0  107.0  182.0   0.0   0.0  120.0  43.0   4.0
2024-08-22  38.0  52.0  107.0  182.0   0.0   0.0  120.0  43.0   4.0
2024-08-23  41.0  61.0    0.0  174.0  96.0   0.0  116.0  45.0  18.0

[664 rows x 9 columns]

# Equal Weighted Portfolios

In [11]:
# portfolio = PortfolioStandard(    
#     capital=200000,
#     name='ETF Buy and Hold Portfolio',    
#     rebalance_iter=RebalancerIter('0 0 * * Fri', 2),
#     tc_model=TransactionCostFutu(),    
#     systems=[
#         # TradingSubSystemSingle(vol_target=vol_target, instruments=['META'],  strategy=[BuyAndHoldStrategy(confidence=1)], max_leverage=max_leverage),
#         # TradingSubSystemSingle(vol_target=vol_target, instruments=['TSLA'],  strategy=[BuyAndHoldStrategy(confidence=1)], max_leverage=max_leverage),
#         # TradingSubSystemSingle(vol_target=vol_target, instruments=['NVDA'],  strategy=[BuyAndHoldStrategy(confidence=1)], max_leverage=max_leverage),
#         # TradingSubSystemSingle(vol_target=vol_target, instruments=['AAPL'],  strategy=[BuyAndHoldStrategy(confidence=1)], max_leverage=max_leverage),
#         TradingSubSystemSingle(vol_target=vol_target, instruments=['EWY'],   strategy=[BuyAndHoldStrategy(confidence=1)], max_leverage=max_leverage),
#         TradingSubSystemSingle(vol_target=vol_target, instruments=['DXJ'],   strategy=[BuyAndHoldStrategy(confidence=2)], max_leverage=max_leverage),        
#         TradingSubSystemSingle(vol_target=vol_target, instruments=['VOE'],   strategy=[BuyAndHoldStrategy(confidence=1)], max_leverage=max_leverage),
#         TradingSubSystemSingle(vol_target=vol_target, instruments=['VBR'],   strategy=[BuyAndHoldStrategy(confidence=1)], max_leverage=max_leverage),
#         TradingSubSystemSingle(vol_target=vol_target, instruments=['BRK-B'], strategy=[BuyAndHoldStrategy(confidence=2)], max_leverage=max_leverage),
#         TradingSubSystemSingle(vol_target=vol_target, instruments=['SPY'],   strategy=[BuyAndHoldStrategy(confidence=1)], max_leverage=max_leverage),
#         TradingSubSystemSingle(vol_target=vol_target, instruments=['QQQ'],   strategy=[BuyAndHoldStrategy(confidence=1)], max_leverage=max_leverage),       
# ])

# portfolio.set_start_date(start_date)
# portfolio.set_end_date(end_date)
# portfolio.backtest_subsystems()
# portfolio.optimize()
# portfolio.backtest()
# portfolio.rebalance()
# portfolio.performance()

# Execute the Portfolio

In [12]:
executor = ExecutorFutu(is_test=False)
executor.set_portfolio(portfolio)
orders = executor.execute(px_interval='5m')
orders

2024-08-24 00:45:50,897 - ExecutorFutu - INFO - market: US
2024-08-24 00:45:50,899 - ExecutorFutu - INFO - Cancel all orders first before executing.....


2024-08-24 00:45:50,908 | 44075 | [open_context_base.py] _send_init_connect_sync:311: InitConnect ok: conn_id=1, host=127.0.0.1, port=11111, user_id=18214795
2024-08-24 00:45:51,087 | 44075 | [open_context_base.py] on_disconnect:383: Disconnected: conn_id=1


2024-08-24 00:45:54,090 - Linear Optimized Portfolio (ETF Buy and Hold Portfolio) - CRITICAL - Portfolio target capital is not specified, use initial backtest capital of $169,336
2024-08-24 00:45:54,092 - Linear Optimized Portfolio (ETF Buy and Hold Portfolio) - INFO - Generate trade position based on target capital of $169,336
2024-08-24 00:45:54,098 - ExecutorFutu - INFO - Execute Linear Optimized Portfolio (ETF Buy and Hold Portfolio) position based on 2024-08-23


2024-08-24 00:45:54,103 | 44075 | [open_context_base.py] _send_init_connect_sync:311: InitConnect ok: conn_id=2, host=127.0.0.1, port=11111, user_id=18214795


2024-08-24 00:45:54,195 - Futu - INFO - 7 Positions: US.TSLA, US.SPY, US.QQQ, US.NVDA, US.META, US.BRK.B, US.AAPL


...

2024-08-24 00:46:11,291 - Futu - INFO - Placed Order: {'code': 'US.SPY', 'price': 557.79, 'qty': 4.0, 'trd_side': 'BUY', 'order_type': 'NORMAL', 'market': 'US', 'trd_env': 'REAL'}


2024-08-24 00:46:11,293 | 44075 | [open_context_base.py] on_disconnect:383: Disconnected: conn_id=8
2024-08-24 00:46:14,309 | 44075 | [open_context_base.py] _send_init_connect_sync:311: InitConnect ok: conn_id=9, host=127.0.0.1, port=11111, user_id=18214795


2024-08-24 00:46:14,571 - Futu - INFO - Placed Order: {'code': 'US.QQQ', 'price': 475.84, 'qty': 14.0, 'trd_side': 'BUY', 'order_type': 'NORMAL', 'market': 'US', 'trd_env': 'REAL'}


2024-08-24 00:46:14,572 | 44075 | [open_context_base.py] on_disconnect:383: Disconnected: conn_id=9


code                  stock_name trd_side order_type order_status   
0  US.META              Meta Platforms      BUY     NORMAL   SUBMITTING  \
0  US.TSLA                         特斯拉      BUY     NORMAL   SUBMITTING   
0  US.NVDA                         英伟达     SELL     NORMAL   SUBMITTING   
0  US.AAPL                          苹果     SELL     NORMAL   SUBMITTING   
0   US.EWY          韩国ETF-iShares MSCI      BUY     NORMAL   SUBMITTING   
0   US.SPY             SPDR 标普500指数ETF      BUY     NORMAL   SUBMITTING   
0   US.QQQ  纳指100ETF-Invesco QQQ Trust      BUY     NORMAL   SUBMITTING   

              order_id    qty   price          create_time   
0  8949918999037653555    4.0  525.86  2024-08-23 12:45:54  \
0  3486117247564381643   11.0  216.06  2024-08-23 12:45:58   
0  1714490234407204816  104.0  127.10  2024-08-23 12:46:01   
0  5915369238059048057    2.0  224.56  2024-08-23 12:46:04   
0  5412689860854084281   96.0   66.61  2024-08-23 12:46:08   
0  7420299009334453437    4.0  557.79  2024-08-23 12:46:11   
0   666962196277423607   14.0  475.84  2024-08-23 12:46:14   

          updated_time  ...   
0  2024-08-23 12:45:54  ...  \
0  2024-08-23 12:45:58  ...   
0  2024-08-23 12:46:01  ...   
0  2024-08-23 12:46:04  ...   
0  2024-08-23 12:46:08  ...   
0  2024-08-23 12:46:11  ...   
0  2024-08-23 12:46:14  ...   

                                              remark  time_in_force   
0  Linear Optimized Portfolio (ETF Buy and Hold P...            DAY  \
0  Linear Optimized Portfolio (ETF Buy and Hold P...            DAY   
0  Linear Optimized Portfolio (ETF Buy and Hold P...            DAY   
0  Linear Optimized Portfolio (ETF Buy and Hold P...            DAY   
0  Linear Optimized Portfolio (ETF Buy and Hold P...            DAY   
0  Linear Optimized Portfolio (ETF Buy and Hold P...            DAY   
0  Linear Optimized Portfolio (ETF Buy and Hold P...            DAY   

  fill_outside_rth aux_price trail_type  trail_value trail_spread currency   
0            False       N/A        N/A          N/A          N/A      USD  \
0            False       N/A        N/A          N/A          N/A      USD   
0            False       N/A        N/A          N/A          N/A      USD   
0            False       N/A        N/A          N/A          N/A      USD   
0            False       N/A        N/A          N/A          N/A      USD   
0            False       N/A        N/A          N/A          N/A      USD   
0            False       N/A        N/A          N/A          N/A      USD   

                                           portfolio       date  
0  Linear Optimized Portfolio (ETF Buy and Hold P... 2024-08-23  
0  Linear Optimized Portfolio (ETF Buy and Hold P... 2024-08-23  
0  Linear Optimized Portfolio (ETF Buy and Hold P... 2024-08-23  
0  Linear Optimized Portfolio (ETF Buy and Hold P... 2024-08-23  
0  Linear Optimized Portfolio (ETF Buy and Hold P... 2024-08-23  
0  Linear Optimized Portfolio (ETF Buy and Hold P... 2024-08-23  
0  Linear Optimized Portfolio (ETF Buy and Hold P... 2024-08-23  

[7 rows x 23 columns]